In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import numpy as np
import keysight.qcs as qcs
from keysight.qcs.experiments import make_calibration_set
from keysight.qcs.experiments import ResonatorSpectroscopy, ResonatorSpectroscopy2D
from simulated_experiments.simulated_experiments import (
    SimulatedResSpectroscopyExperiment,
)

In [3]:
# Set this to True if channel mapper exists
channel_mapper_exists = False

if channel_mapper_exists:
    mapper = qcs.load("<path/to/channel_mapper.qcs>")
else:
    # generate an empty channel mapper with the correct address
    mapper = qcs.ChannelMapper("127.0.0.1")

# Generate the calibration_set template
calibration_set = make_calibration_set(qubits=1)

# Set this to True if connected to hardware
run_on_hw = False

In [4]:
# Define the number of qubits
n_qubits = 1
qubits = qcs.Qudits(range(n_qubits))

# Create a resonator spectroscopy experiment
res_spectroscopy = ResonatorSpectroscopy(
    backend=mapper,
    calibration_set=calibration_set,
    qubits=qubits,
    operation="measurement",
)

In [5]:
# Draw the program to view the hardware operations
res_spectroscopy.draw()

In [6]:
# Retrieve the readout frequencies stored in the calibration set
current_freq = res_spectroscopy.calibration_set.variables.readout_frequencies[
    list(qubits.labels)
].value

# Set the frequency range for sweeping
start_frequency = current_freq - 200e6
end_frequency = current_freq + 200e6
steps = 9
freq_scan_values = np.linspace(start_frequency, end_frequency, steps)

In [7]:
# Configure the repetitions for this experiment
res_spectroscopy.configure_repetitions(
    frequencies=freq_scan_values, n_shots=1, frequency_name="readout_frequencies"
)

In [8]:
# View the waveforms to be executed on the hardware
res_spectroscopy.compiled_program.render(
    channel_subplots=False, lo_frequency=5e9, sweep_index=4, sample_rate=5e9
)

In [9]:
if run_on_hw:
    res_spectroscopy.execute()
else:
    # load in a previously executed version of this experiment
    res_spectroscopy = qcs.load("ReadoutSpectroscopy.qcs")

In [10]:
# Plot the trace waveforms
res_spectroscopy.plot_trace()

In [11]:
res_spectroscopy = SimulatedResSpectroscopyExperiment(calibration_set, qubits)

In [12]:
res_spectroscopy.plot_iq(plot_type="linear")

In [13]:
ec = res_spectroscopy.fit()

# View the data format of the estimate
print(ec.estimates[0])

Estimate(amplitude=0.0004993143040154964, resonance=5149864062.317179, kappa=19867396.139514126, offset_real=-0.026998284919072184, ...)


In [14]:
res_spectroscopy.plot()

In [15]:
res_spectroscopy.get_updated_calibration_values()

{'readout_frequencies': 5149864062.317179}

In [16]:
res_spectroscopy.calibration_set.variables.readout_frequencies.value

array([5.15e+09])

In [17]:
res_spectroscopy.set_updated_calibration_values()

# Print the value of the variable to confirm the update
res_spectroscopy.calibration_set.variables.readout_frequencies.value

array([5.14986406e+09])

In [18]:
# Define the number of qubits and the calibration set
n_qubits = [0, 1]
qubits = qcs.Qudits(n_qubits)
calibration_set = make_calibration_set(qubits=len(qubits))

In [19]:
# Create a resonator spectroscopy experiment
res_spectroscopy2D = ResonatorSpectroscopy2D(
    backend=mapper,
    calibration_set=calibration_set,
    qubits=qubits,
    operation="measurement",
)

In [20]:
# Draw the program to view the operations to be performed on hardware
res_spectroscopy2D.draw()

In [21]:
# Retrieve the readout frequencies stored in the calibration set for the target qubits
current_freq = res_spectroscopy2D.calibration_set.variables.readout_frequencies[
    [0, 1]
].value

# Set the range for sweeping the readout pulse frequency
start_frequency = current_freq - 200e6
end_frequency = current_freq + 200e6
freq_steps = 9
freq_scan_values = np.linspace(start_frequency, end_frequency, freq_steps)

In [22]:
# Set the range for sweeping the readout pulse amplitude (units = V)
start_amplitude = 0.1 if len(qubits) == 1 else [0.1] * len(qubits)
end_amplitude = 1 if len(qubits) == 1 else [1] * len(qubits)
ampl_steps = 10
ampl_scan_values = np.linspace(start_amplitude, end_amplitude, ampl_steps)

In [23]:
# Configure the repetitions for this experiment
res_spectroscopy2D.configure_repetitions(
    frequencies=freq_scan_values,
    frequency_name="readout_frequencies",
    amplitudes=ampl_scan_values,
    amplitude_name="readout_pulse_amplitudes",
    n_shots=1,
)

In [24]:
# View the waveforms to be executed on the hardware
res_spectroscopy2D.compiled_program.render(
    channel_subplots=False, lo_frequency=5e9, sweep_index=(5, 5), sample_rate=5e9
)

In [25]:
if run_on_hw:
    res_spectroscopy2D.execute()
else:
    # load in a previously executed version of this experiment
    res_spectroscopy2D = qcs.load("ReadoutSpectroscopy2D.qcs")

In [26]:
# Plot the trace waveforms
res_spectroscopy2D.plot_trace()

In [27]:
# Plot the IQ data as a heatmap
res_spectroscopy2D.plot_iq(plot_type="2d")